In [9]:
from IPython import get_ipython
get_ipython().magic('reset -sf')


In [10]:
import numpy as np
import pandas as pd
from sklearn.preprocessing import StandardScaler
from sklearn.base import BaseEstimator, ClassifierMixin
from scipy.optimize import minimize, LinearConstraint, NonlinearConstraint
from scipy import stats
import pickle

In [11]:
## 划分测试集和训练集
train_ratio = 0.8 # 训练集比例

data = pd.read_csv('seeds_dataset.txt', header=None, delim_whitespace=True) # delim_whitespace=True表示分割符为空白字符
data.info

labels = data.iloc[:, -1]
classes = labels.unique()
trainData = pd.DataFrame(data=None, index=None)
testData = pd.DataFrame(data=None, index=None)

for i in classes:
    classData = data.loc[labels==i, :]
    numTrain = round(train_ratio*classData.shape[0]) # 训练集样本数
    indices = np.random.permutation(classData.shape[0])
    
    trainData = pd.concat([trainData, classData.iloc[indices[0:numTrain], :]])
    testData = pd.concat([testData, classData.iloc[indices[numTrain:], :]])

trainData.info
testData.info                                            
trainData.to_csv('trainData.csv', header=0, index=0, sep='\t')
testData.to_csv('testData.csv', header=0, index=0, sep='\t')


In [12]:
## 获取训练和训练数据及归一化
X_train = trainData.iloc[:, :-1]
Y_train = trainData.iloc[:, -1].values
X_test = testData.iloc[:, :-1]
Y_test = testData.iloc[:, -1].values

# 使用StandardScaler类归一化
scaler = StandardScaler()
X_train_scaled = scaler.fit_transform(X_train)
X_test_scaled = scaler.transform(X_test)


In [13]:
## 定义超圆盘分类器类
class NHCmodel(BaseEstimator, ClassifierMixin):
    def __init__(self, ) -> None:
        super().__init__()
        self.classes = 0
        self.s_r = {}
        self.classifiers = {}
        self.predictData = None
        self.accuracy = 0

    @staticmethod
    def gaussian_kernel(x, y, sigma=0.25):
        return np.exp(-np.linalg.norm(x-y, ord=2, axis=1)**2 / (2 * (sigma ** 2)))
    
    @staticmethod
    def Objective_Function1(beta, X):
        """返回超圆盘的对偶问题的目标函数，在某一拉格朗日系数下的值
        Args:
            beta (ndarray): 为该输入样本集合下的拉格朗日系数
            X (ndarray): X为输入样本矩阵, 行为样本个数, 列为样本特征
        """
        beta = beta.reshape(-1, 1)
        print(X)
        return np.sum(beta*np.sum(X*X, 1).reshape(-1, 1))-np.sum((beta*X)@((beta*X).T))
    
    @staticmethod
    def Objective_Function2(alpha, X_plus, X_minus):
        M_plus  = np.shape(X_plus)[0]
        alpha_plus = alpha[:M_plus]
        alpha_minus = alpha[M_plus:]
        M_minus = np.size(alpha_minus)
        result = 0
        for i in range(M_plus):
            result = result + np.sum(alpha_plus[i]*alpha_plus*NHCmodel.gaussian_kernel(X_plus[i, :], X_plus))
            - 2*np.sum(alpha_plus[i]*alpha_minus*NHCmodel.gaussian_kernel(X_plus[i, :], X_minus))
        for i in range(M_minus):
            result = result + np.sum(alpha_minus[i]*alpha_minus*NHCmodel.gaussian_kernel(X_minus[i, :], X_minus))
        return result
    
    @staticmethod
    def nonlcon(alpha, beta_plus, beta_minus, X_plus, X_minus, r_plus, r_minus):
        M_plus  = np.shape(X_plus)[0]
        alpha_plus = alpha[:M_plus]
        alpha_minus = alpha[M_plus:]
        M_minus = np.size(alpha_minus)
        
        c = np.zeros((2, 1))
        for i in range(M_plus):
            c[0] = c[0] + np.sum(alpha_plus[i]*alpha_plus*NHCmodel.gaussian_kernel(X_plus[i, :],X_plus))
            - np.sum(alpha_plus[i]*beta_plus*NHCmodel.gaussian_kernel(X_plus[i, :], X_plus))
            + np.sum(beta_plus[i]*beta_plus*NHCmodel.gaussian_kernel(X_plus[i, :], X_plus))
        c[0] -= r_plus**2
        for i in range(M_minus):
            c[0] = c[0] + np.sum(alpha_minus[i]*alpha_minus*NHCmodel.gaussian_kernel(X_minus[i, :],X_minus))
            - np.sum(alpha_minus[i]*beta_minus*NHCmodel.gaussian_kernel(X_minus[i, :], X_minus))
            + np.sum(beta_minus[i]*beta_minus*NHCmodel.gaussian_kernel(X_minus[i, :], X_minus))
        c[1] -= r_minus**2
        return c.flatten()

    def fit(self, X, y):
        # 拟合函数
        classes = np.unique(y)
        Num = np.size(classes)
        beta = np.zeros((Num, np.size(y)))
        s_and_r = np.ones((Num, np.shape(X)[1]+1))
        # 分类求解超圆盘对偶问题拉格朗日系数，以求解s和r
        for i in classes:
            Xx = X[y==i, :]
            M = np.shape(Xx)[0]
            # 设定拉格朗日系数beta初值,一个样本一个beta
            beta_init = np.ones((M, 1)) / M # 一维数组，但是在优化函数里面需要reshape乘二维数组才能运算
            # 设线性等式约束
            Aeq1 = np.ones((1, M))
            beq1 = np.array([1])
            linearConstraint1 = LinearConstraint(Aeq1, beq1, beq1)
            # 设定beta下界
            bounds = [(1e-6, None) for _ in range(M)] 
            # 求解beta
            result1 = minimize(NHCmodel.Objective_Function1, beta_init, 
                            args=(Xx,), method='SLSQP', bounds=bounds, constraints=linearConstraint1,
                            )
            beta[i-1, :M] = result1.x
            
            s = np.sum(result1.x.reshape(-1, 1)*Xx, 0)
            r = np.max(np.linalg.norm(Xx-s, ord=2,axis=1))
            s_and_r[i-1, :] = np.concatenate([s, [r]])
            
            self.s_r = {'s': s,
                        'r': r}
        # 求解多个分类器的参数，即分类超平面参数，OVO策略
        Num_classifier = int(Num*(Num-1)/2)
        b_classifier = np.zeros((Num_classifier, 1))
        iter = 0
        for i in range(Num-1):
            for j in range(i+1, Num):
                iter += 1
                # 获取基本信息
                X_plus = X[y==i+1, :]
                X_minus = X[y==j+1, :]
                M_plus = np.shape(X_plus)[0]
                M_minus = np.shape(X_minus)[0]
                # 设定超平面参数初值，都为列
                alpha_plus = np.ones((M_plus, 1)) / M_plus
                alpha_minus = np.ones((M_minus, 1)) / M_minus
                alpha_init = np.concatenate((alpha_plus, alpha_minus), axis=0)
                # 设定线性等式约束
                Aeq2 = np.zeros((2, M_plus+M_minus))
                Aeq2[0,:M_plus] = 1;
                Aeq2[1, M_plus:] = 1
                beq2 = np.array([1, 1])
                linearConstraint2 = LinearConstraint(Aeq2, beq2, beq2)
                # 设定不等式约束
                r_plus = s_and_r[i, -1]
                r_minus = s_and_r[j, -1]
                beta_plus = beta[i, :M_plus]
                beta_minus = beta[j, :M_minus]
                lb = -np.inf
                ub = np.array([0, 0])
                # NonlinearConstraint(lambda x: NHCmodel.nonlcon(x, beta_plus, beta_minus, X_plus, X_minus, r_plus_minus), lb, ub)
                # 这个和@(beta)Objective_Function1(beta, X),@(beta) 表示输入要优化的值为beta，X不动，异曲同工
                nonlinearConstraint =  NonlinearConstraint(lambda x: NHCmodel.nonlcon(x, beta_plus, beta_minus, X_plus, X_minus, r_plus, r_minus), lb, ub)
                constraints = [linearConstraint2, nonlinearConstraint]
                # 求解alpha
                result2 = minimize(NHCmodel.Objective_Function2, alpha_init, args=(X_plus, X_minus,),
                                   method='SLSQP', constraints=constraints)
                alpha = result2.x
                alpha_plus = alpha[:M_plus]
                alpha_minus = alpha[M_plus:]
                # 求解b
                for k in range(M_plus):
                    b_classifier[iter-1] += np.sum(alpha_plus[k]*alpha_plus*NHCmodel.gaussian_kernel(X_plus[k, :], X_plus))
                for k in range(M_minus):
                    b_classifier[iter-1] -= np.sum(alpha_minus[k]*alpha_minus*NHCmodel.gaussian_kernel(X_minus[k, :], X_minus))
                b_classifier[iter-1] = -1/2*b_classifier[iter-1]
                b = b_classifier[iter-1]
                self.classes = Num
                self.classifiers[(i+1, j+1)] = {'X+': X_plus,
                                                'X-': X_minus,
                                                'alpha+': alpha_plus,
                                                'alpha-': alpha_minus,
                                                'b': b}    
        # 保存分类器参数字典
        with open('classifiers.pkl', 'wb') as f:
            pickle.dump(self.classifiers, f)
                                                
        return 0  
                

    def predict(self,X, y):
        fx = np.zeros((np.shape(X)[0], self.classes))
        indexclasses = 0
        fxij = np.zeros((np.shape(X)[0], self.classes))
        for (i, j), classifier in self.classifiers.items():
            indexclasses += 1
            X_pl = classifier['X+']
            X_mi = classifier['X-']
            alpha_pl = classifier['alpha+']
            alpha_mi = classifier['alpha-']
            bb = classifier['b']
            
            M_plus = np.shape(X_pl)[0]
            M_minus = np.shape(X_mi)[0]
            
            for g in range(M_plus):
                fx[:, indexclasses-1] = fx[:, indexclasses-1] + alpha_pl[g]*NHCmodel.gaussian_kernel(X_pl[g, :], X).reshape(-1)
            for g in range(M_minus):
                fx[:, indexclasses-1] = fx[:, indexclasses-1] - alpha_mi[g]*NHCmodel.gaussian_kernel(X_mi[g, :], X).reshape(-1)
            
            fx[:, indexclasses-1] = np.sign(fx[:, indexclasses-1] + bb)
            fxij[:, indexclasses-1] = fx[:, indexclasses-1] 
            fx[:, indexclasses-1][fx[:, indexclasses-1]==1] = i
            fx[:, indexclasses-1][fx[:, indexclasses-1]==-1] = j
            fx[:, indexclasses-1][fx[:, indexclasses-1]==0] = 0


        y_pred = np.apply_along_axis(lambda x: np.argmax(np.bincount(x.astype(int))), axis=1, arr=fx) # axis表示假如你是n×m维度，axis=0，表示在n方向上，axis=1，表示在m方向上
        accuray = np.sum(y_pred==y) / np.size(y)
        y = y.reshape(-1, 1)
        y_pred = y_pred.reshape(-1, 1)
        self.predictData = np.concatenate((X, y, y_pred, fxij, fx), axis=1)
        self.accuracy = accuray
        print('accuray = ', accuray)
        return y_pred
              

In [14]:
## 训练
model = NHCmodel()
model.fit(X_train_scaled, Y_train)

C:\Users\lenovo\AppData\Local\Temp\ipykernel_7556\424054626.py:79: DeprecationWarning: Use of `minimize` with `x0.ndim != 1` is deprecated. Currently, singleton dimensions will be removed from `x0`, but an error will be raised in SciPy 1.11.0.
  result1 = minimize(NHCmodel.Objective_Function1, beta_init,


[[-0.20088596 -0.29980303  0.95601192 -0.51532739  0.09586186  1.96103481
  -0.82466636]
 [-0.0240302  -0.03471404  0.45455894  0.06066802  0.06987381 -0.38789669
  -0.20131472]
 [-0.85389187 -1.04205223  0.86898289 -1.22920587 -0.56943212 -0.31689624
  -1.62611845]
 [-0.28591277 -0.30737701  0.34266447 -0.42414665 -0.15622219 -1.30498581
  -0.82466636]
 [-0.67703611 -0.80725912  0.68663635 -1.08909887 -0.36932417 -0.88752947
  -1.62207071]
 [-0.56139964 -0.54974409 -0.13806731 -0.51977523 -0.49666559  0.29909839
  -0.64858976]
 [-0.29951706 -0.55731806  1.94648516 -1.13357728  0.31676025  1.00713064
  -1.26991752]
 [-0.72805219 -0.61790983 -1.05808848 -0.48196858 -0.98524086 -0.11112642
  -0.69109101]
 [ 0.59836606  0.67723928  0.13959673  0.94356446  0.52986223 -1.09264188
   0.94824283]
 [-0.25870419 -0.23163729  0.03599075 -0.24178517 -0.24198274 -0.66663919
  -0.38346293]
 [-0.1838806  -0.21648935  0.48771285 -0.27736789 -0.1614198  -0.24589579
  -0.37334358]
 [-0.29271492 -0.2089

C:\Users\lenovo\AppData\Local\Temp\ipykernel_7556\424054626.py:79: DeprecationWarning: Use of `minimize` with `x0.ndim != 1` is deprecated. Currently, singleton dimensions will be removed from `x0`, but an error will be raised in SciPy 1.11.0.
  result1 = minimize(NHCmodel.Objective_Function1, beta_init,


[[ 1.50985347  1.53309804  0.42140502  1.58405356  1.42644982 -0.14794147
   1.67885951]
 [ 1.56086956  1.4649323   1.12592573  1.07699969  1.6395518   0.39836753
   1.21539353]
 [ 0.38069742  0.24552291  1.45332065 -0.59094068  0.83392237 -0.2406365
  -0.5352531 ]
 [ 1.3091902   1.34374876  0.40068382  1.31273526  1.09900044 -0.99534497
   1.39349399]
 [ 1.3091902   1.23013919  1.09277182  0.83904019  1.54859364  1.06629768
   0.95229057]
 [ 0.17323201  0.07132156  1.14664693 -0.33741375  0.52986223 -0.06707985
   0.06178824]
 [ 0.91126472  0.8287187   1.15079117  0.36089729  1.11459327  1.09390896
   0.51108714]
 [ 1.06091191  0.98019813  1.15493541  0.58106542  1.12498849 -1.07423436
   0.86728807]
 [ 1.25137197  1.2528611   0.62861699  1.16595651  1.0730124  -1.29118017
   0.9826486 ]
 [ 0.52354247  0.51818588  0.63276123  0.19855109  0.68579051  0.33854308
   0.42406078]
 [ 1.38741487  1.40434053  0.47942437  1.37722895  1.28351557 -0.21959933
   1.49671131]
 [ 0.46232316  0.46516

d:\software\Anaconda3\lib\site-packages\scipy\optimize\_optimize.py:284: RuntimeWarning: Values in x were outside bounds during a minimize step, clipping to bounds
  warnings.warn("Values in x were outside bounds during a "
C:\Users\lenovo\AppData\Local\Temp\ipykernel_7556\424054626.py:79: DeprecationWarning: Use of `minimize` with `x0.ndim != 1` is deprecated. Currently, singleton dimensions will be removed from `x0`, but an error will be raised in SciPy 1.11.0.
  result1 = minimize(NHCmodel.Objective_Function1, beta_init,


[[ 1.50985347  1.53309804  0.42140502  1.58405356  1.42644982 -0.14794147
   1.67885951]
 [ 1.56086956  1.4649323   1.12592573  1.07699969  1.6395518   0.39836753
   1.21539353]
 [ 0.38069742  0.24552291  1.45332065 -0.59094068  0.83392237 -0.2406365
  -0.5352531 ]
 [ 1.3091902   1.34374876  0.40068382  1.31273526  1.09900044 -0.99534497
   1.39349399]
 [ 1.3091902   1.23013919  1.09277182  0.83904019  1.54859364  1.06629768
   0.95229057]
 [ 0.17323201  0.07132156  1.14664693 -0.33741375  0.52986223 -0.06707985
   0.06178824]
 [ 0.91126472  0.8287187   1.15079117  0.36089729  1.11459327  1.09390896
   0.51108714]
 [ 1.06091191  0.98019813  1.15493541  0.58106542  1.12498849 -1.07423436
   0.86728807]
 [ 1.25137197  1.2528611   0.62861699  1.16595651  1.0730124  -1.29118017
   0.9826486 ]
 [ 0.52354247  0.51818588  0.63276123  0.19855109  0.68579051  0.33854308
   0.42406078]
 [ 1.38741487  1.40434053  0.47942437  1.37722895  1.28351557 -0.21959933
   1.49671131]
 [ 0.46232316  0.46516

d:\software\Anaconda3\lib\site-packages\scipy\optimize\_optimize.py:284: RuntimeWarning: Values in x were outside bounds during a minimize step, clipping to bounds
  warnings.warn("Values in x were outside bounds during a "


[[-1.2450152  -1.08749606 -2.26406217 -0.77775    -1.49200776  1.62181044
  -0.27012627]
 [-1.02054442 -1.17080974  0.33852023 -1.10466632 -0.80072574 -0.06905208
  -0.55953953]
 [-1.19399912 -1.14808783 -1.37305068 -1.00903774 -1.31528905  0.22744053
  -0.2944127 ]
 [-0.56820179 -0.68607558  0.70321331 -0.87337859 -0.07565925  3.03261565
  -0.71335356]
 [-1.17019161 -1.08749606 -1.56782994 -1.00681382 -1.40884602 -0.97365039
  -0.55953953]
 [-0.67363503 -0.60276189 -0.7141166  -0.29738318 -0.611013    1.63232903
  -0.18714764]
 [-0.96952833 -0.93601663 -0.8715977  -0.61985165 -1.1723548   0.37404331
  -0.20333859]
 [-0.82668329 -0.73909337 -1.04151152 -0.68879319 -0.94625879  0.80333305
  -0.28024561]
 [-0.52058677 -0.4664304  -0.38672168 -0.53311875 -0.48627038  1.50742083
  -0.20536246]
 [-0.84708973 -0.85270295 -0.43230832 -0.91118523 -0.70716877  1.16359459
  -0.73561612]
 [-1.37765703 -1.3147152  -1.89522486 -0.99791813 -1.64013963  0.75665683
  -0.64656589]
 [-1.22800984 -1.1783

C:\Users\lenovo\AppData\Local\Temp\ipykernel_7556\424054626.py:124: DeprecationWarning: Use of `minimize` with `x0.ndim != 1` is deprecated. Currently, singleton dimensions will be removed from `x0`, but an error will be raised in SciPy 1.11.0.
  result2 = minimize(NHCmodel.Objective_Function2, alpha_init, args=(X_plus, X_minus,),
C:\Users\lenovo\AppData\Local\Temp\ipykernel_7556\424054626.py:124: DeprecationWarning: Use of `minimize` with `x0.ndim != 1` is deprecated. Currently, singleton dimensions will be removed from `x0`, but an error will be raised in SciPy 1.11.0.
  result2 = minimize(NHCmodel.Objective_Function2, alpha_init, args=(X_plus, X_minus,),
C:\Users\lenovo\AppData\Local\Temp\ipykernel_7556\424054626.py:124: DeprecationWarning: Use of `minimize` with `x0.ndim != 1` is deprecated. Currently, singleton dimensions will be removed from `x0`, but an error will be raised in SciPy 1.11.0.
  result2 = minimize(NHCmodel.Objective_Function2, alpha_init, args=(X_plus, X_minus,),


0

In [15]:
# 测试
model.predict(X_test_scaled, Y_test)

accuray =  0.8809523809523809


array([[1],
       [1],
       [1],
       [1],
       [1],
       [1],
       [1],
       [3],
       [1],
       [3],
       [1],
       [1],
       [1],
       [1],
       [2],
       [2],
       [2],
       [2],
       [2],
       [2],
       [2],
       [2],
       [2],
       [2],
       [2],
       [2],
       [2],
       [2],
       [3],
       [3],
       [3],
       [3],
       [3],
       [3],
       [1],
       [3],
       [3],
       [1],
       [3],
       [3],
       [3],
       [1]], dtype=int64)

In [16]:
predictdata = model.predictData